In [2]:
import os
os.environ['HF_HOME'] = "/scratch/tar3kh/models/cache"
import torch 
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline
from datasets import load_dataset #datasets is huggingface's dataset package
from peft import get_peft_model, LoraConfig, TaskType
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import PIL

import lm_eval

In [5]:
tokenizer = AutoTokenizer.from_pretrained("TheFinAI/Fino1-8B")
model = AutoModelForCausalLM.from_pretrained("ThinkTim21/FinPlan-1")

model.safetensors.index.json:   0%|          | 0.00/23.9k [00:00<?, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

In [6]:
# Prepare the model and tokenizer 
tokenizer.pad_token = tokenizer.eos_token # set padding token to EOS token
model.config.poad_token_id = tokenizer.pad_token_id # set the padding token for model

In [7]:
budget = pd.read_csv("budget_dataset.csv")
goals = pd.read_csv("goals_dataset.csv")


In [8]:
budget['instruct_lora'] = budget.apply(
    lambda row: f"Q: {row['question']}\n\nA: ",
    axis=1
)

goals['instruct_lora'] = goals.apply(
    lambda row: f"Q: {row['question']}\n\nA: ",
    axis=1
)

In [9]:
from datasets import load_dataset, Dataset #datasets is huggingface's dataset package
budget = budget.sample(frac = 1, random_state = 42) # randomly shuffle DF
train_budget = budget[:2500]
val_budget = budget[2500:]
train_budget = Dataset.from_pandas(train_budget)
val_budget = Dataset.from_pandas(val_budget)
train_budget = train_budget.map(lambda samples: tokenizer(samples['instruct']), batched = True)
val_budget = val_budget.map(lambda samples: tokenizer(samples['instruct']), batched = True)

Map:   0%|          | 0/2500 [00:00<?, ? examples/s]

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

In [10]:
goals = goals.sample(frac = 1, random_state = 42) # randomly shuffle DF
train_goals = goals[:2500]
val_goals = goals[2500:]
train_goals = Dataset.from_pandas(train_goals)
val_goals = Dataset.from_pandas(val_goals)
train_goals = train_goals.map(lambda samples: tokenizer(samples['instruct']), batched = True)
val_goals = val_goals.map(lambda samples: tokenizer(samples['instruct']), batched = True)

Map:   0%|          | 0/2500 [00:00<?, ? examples/s]

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

In [11]:
formatted_prompt = f"Q: {val_goals[0]['question']}\n\nA: "
inputs = tokenizer.encode(formatted_prompt, return_tensors = "pt").to(model.device)
output = model.generate(inputs, max_new_tokens = 800, pad_token_id = tokenizer.pad_token_id, do_sample = False)
generated_text = tokenizer.decode(output[0], skip_special_tokens = True)
print(generated_text)

/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:636: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


Q: My short term goal is to save for a $1774 vacation in the next year, my medium term goal is to save for down payment for a new car, around 5227 in the next 2 or 3 years, and my long term goal is to save for a down payment for a house around 151861 in the next ten years, can you help me integrate these goals into my budget as well as where I should store these savings?

A:  Thinking

Alright, let's figure out how to make these savings goals work with your budget. First, I want to make sure I understand what you're aiming for. You've got three goals: saving for a vacation, a new car, and eventually a house. Let's break each down.

For the vacation, you're looking to save $1774 in the next year. That's a pretty manageable goal, especially if you break it down into monthly chunks. Let's see, $1774 divided by 12 months gives you about $147.83 per month. Not too bad, right?

Next up is saving for a new car. You're aiming for $5227 in 2-3 years. That's a bit longer, so let's spread it out.

In [ ]:
formatted_prompt = f"Q: {val_budget[0]['question']}\n\nA: "
inputs = tokenizer.encode(formatted_prompt, return_tensors = "pt").to(model.device)
output = model.generate(inputs, max_new_tokens = 800, pad_token_id = tokenizer.pad_token_id, do_sample = False)
generated_text = tokenizer.decode(output[0], skip_special_tokens = True)
print(generated_text)